# Reward function examples

<p style="display: flex; justify-content: space-between; align-items: center;">
    <b>Unit 03. Reward function examples</b>
    <span><b>Section 08. Reward Function</b></span>
</p>

---
<h3 style="display: flex; justify-content: space-between; align-items: center;">
    PPT

</h3>

<div style="position:relative; width:100%; padding-bottom:65%;">
    <iframe 
        src="https://drive.google.com/file/d/1JtZbLQ5DqgzB6vSg1-PpJR_jnFWiNCEs/preview" 
        style="position:absolute; top:0; left:0; width:100%; height:100%"></iframe>
</div>


---
<h3 style="display: flex; justify-content: space-between; align-items: center;">
    Video
    <span style="font-size: 0.7em;">
        <a href="../premium/01.html" target="_blank" title="This video can only be viewed by accounts registered in the premium course">🚀 Premium Course </a> 
    </span>
    <span style="font-size: 0.6em;">
        <a title="English, Deutsch, Español, Français, Bahasa Indonesia, Italiano, 日本語, 한국어, Nederlands, Polski, Português, Русский, ภาษาไทย,Türkçe,Tiếng Việt, 简体中文, 繁體中文, हिन्दी, العربية"><i class="fa fa-info-circle"></i> subtitles in 20 languages</a>
    </span>
</h3>

<div style="position:relative; width:100%; padding-bottom:65%;">
    <iframe 
        src="https://drive.google.com/file/d/10LHu7W8Jm5AD9gx2e_VEzbUP13RTAezw/preview" 
        style="position:absolute; top:0; left:0; width:100%; height:100%"></iframe>
</div>


```{important}
- We strongly recommend using **Google Chrome web browser** for the video.
- The video can only be viewed on a Google account registered for the **premium course**.
  - Can't see the video even though you're registered for the premium course?  
  - <a href="../premium/04.html" target="_blank">Troubleshooting Video Playback Issues</a>
- **Add Q&A comments**: You can write a question comment on the video by clicking the `Pop out` button in the top right corner of the video.
```

## Resources

### Example 1
- Time trial - follow the center line
```python3
def reward_function(params):
    '''
    Example of rewarding the agent to follow center line
    '''
    
    # Read input parameters
    track_width = params['track_width']
    distance_from_center = params['distance_from_center']
    
    # Calculate 3 markers that are at varying distances away from the center line
    marker_1 = 0.1 * track_width
    marker_2 = 0.25 * track_width
    marker_3 = 0.5 * track_width
    
    # Give higher reward if the car is closer to center line and vice versa
    if distance_from_center <= marker_1:
        reward = 1.0
    elif distance_from_center <= marker_2:
        reward = 0.5
    elif distance_from_center <= marker_3:
        reward = 0.1
    else:
        reward = 1e-3  # likely crashed/ close to off track
    
    return float(reward)
```

### Example 2
- Time trial - stay inside the two borders
```python3
def reward_function(params):
    '''
    Example of rewarding the agent to stay inside the two borders of the track
    '''
    
    # Read input parameters
    all_wheels_on_track = params['all_wheels_on_track']
    distance_from_center = params['distance_from_center']
    track_width = params['track_width']
    
    # Give a very low reward by default
    reward = 1e-3

    # Give a high reward if no wheels go off the track and
    # the agent is somewhere in between the track borders
    if all_wheels_on_track and (0.5*track_width - distance_from_center) >= 0.05:
        reward = 1.0

    # Always return a float value
    return float(reward)
```

### Example 3
- Time trial - prevent zig-zag
```python3
def reward_function(params):
    '''
    Example of penalize steering, which helps mitigate zig-zag behaviors
    '''

    # Read input parameters
    distance_from_center = params['distance_from_center']
    track_width = params['track_width']
    abs_steering = abs(params['steering_angle']) # Only need the absolute steering angle

    # Calculate 3 marks that are farther and father away from the center line
    marker_1 = 0.1 * track_width
    marker_2 = 0.25 * track_width
    marker_3 = 0.5 * track_width

    # Give higher reward if the car is closer to center line and vice versa
    if distance_from_center <= marker_1:
        reward = 1.0
    elif distance_from_center <= marker_2:
        reward = 0.5
    elif distance_from_center <= marker_3:
        reward = 0.1
    else:
        reward = 1e-3  # likely crashed/ close to off track

    # Steering penality threshold, change the number based on your action space setting
    ABS_STEERING_THRESHOLD = 15 
    
    # Penalize reward if the car is steering too much
    if abs_steering > ABS_STEERING_THRESHOLD:
        reward *= 0.8
    return float(reward)
```

### Example 4
- Object avoidance and head-to-head - stay on one lane and not crashing (default for OA and h2h)
- [Link](https://docs.aws.amazon.com/deepracer/latest/developerguide/deepracer-reward-function-examples.html#deepracer-reward-function-example-3)
```python3
import math
def reward_function(params):
    '''
    Example of rewarding the agent to stay inside two borders
    and penalizing getting too close to the objects in front
    '''
    all_wheels_on_track = params['all_wheels_on_track']
    distance_from_center = params['distance_from_center']
    track_width = params['track_width']
    objects_location = params['objects_location']
    agent_x = params['x']
    agent_y = params['y']
    _, next_object_index = params['closest_objects']
    objects_left_of_center = params['objects_left_of_center']
    is_left_of_center = params['is_left_of_center']
    # Initialize reward with a small number but not zero
    # because zero means off-track or crashed
    reward = 1e-3
    # Reward if the agent stays inside the two borders of the track
    if all_wheels_on_track and (0.5 * track_width - distance_from_center) >= 0.05:
        reward_lane = 1.0
    else:
        reward_lane = 1e-3
    # Penalize if the agent is too close to the next object
    reward_avoid = 1.0
    # Distance to the next object
    next_object_loc = objects_location[next_object_index]
    distance_closest_object = math.sqrt((agent_x - next_object_loc[0])**2 + (agent_y - next_object_loc[1])**2)
    # Decide if the agent and the next object is on the same lane
    is_same_lane = objects_left_of_center[next_object_index] == is_left_of_center
    if is_same_lane:
        if 0.5 <= distance_closest_object < 0.8:
            reward_avoid *= 0.5
        elif 0.3 <= distance_closest_object < 0.5:
            reward_avoid *= 0.2
        elif distance_closest_object < 0.3:
            reward_avoid = 1e-3  # Likely crashed
    # Calculate reward by putting different weights on
    # the two aspects above
    reward += 1.0 * reward_lane + 4.0 * reward_avoid
    return reward
```